<a href="https://colab.research.google.com/github/ChabbyTMD/668_Unix_project/blob/main/BIOL668_FINALPROJECT.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# BIOL 668 FINAL PROJECT.

## Introduction

A recent WHO report estimated that Uganda accounts for 5.1% of all Malaria cases globally. Current vector control strategies include the wide spread use of long lasting insecticide treated nets(LLIN), indoor residual spraying with insecticides(IRS).

Historically, the most commonly used class of insecticide for treating mosquito nets are pythreroids specifically delatamethrin while alpha-cypermethrin is utlised for indoor residual spraying. In recent decades other classes of insecticides have been introduced i.e. carbamates, organophospates and organochlorines.

The long time use of a limited number of insecticide classes in Uganda introduces evolutionary pressure. Mosquito's adaptations to exposure to these insecticide compounds leave behind signatures in their genomes. The H12 metric, developed by Garud et al[citation needed] is a measure of haplotype homozygosity. It allows for a naive scanning of the entire genome for signatures of hard and soft sweeps that are indicattive of postive selection. These regions could provide clues as to the loci that could confer resistance to insecticide compounds.

In this analysis we aim to identify regions of the *Anopheles gambiae* genome under positive selection. Subsequently, we aim to identify genes under positive selection and search current literature for their association to insecticide resistance.

## MalariaGEN Data Import.

Below we import the necessary API's and data packages to analyze sequence data in the malariaGEN data resource.

In [ ]:
# Install malariagen data package and import the MalariaGEN API
!pip install -q --no-warn-conflicts malariagen_data
import malariagen_data

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 159.9/159.9 kB 1.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 3.1/3.1 MB 2.8 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.2/44.2 MB 3.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.5/7.5 MB 3.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 4.0/4.0 MB 4.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 302.5/302.5 kB 3.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 142.5/142.5 kB 2.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 24.4/24.4 MB 2.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.1/8.1 MB 3.3 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 209.7/209.7 kB 3.4 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 7.7/7.7 MB 3.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.6/1.6 MB 3.8 MB/s eta 0:00:00


In [ ]:
# Mounting Google drive to act as a store for data objects and results.
try:
    from google.colab import drive
    drive.mount("drive")
except ImportError:
    pass

results_dir = "drive/MyDrive/malariagen_data_cache"

Mounted at drive


## Create MalariaGEN data object.

> **NOTE:** In order to access malariaGEN data one has to register their google account data at the google form https://forms.gle/kCqistorZyxaU4LP7 .

Once registered it takes a couple of hours for your google account to receive authentication for the Google storage buckets. Otherwise you'll get an error running this cell. But if it runs with no errors then your google account details have been successfully registered with MalariaGEN vector observatory.

In [ ]:
# Create the malariaGEN data object.

ag3 = malariagen_data.Ag3(results_cache=results_dir)
ag3

<MalariaGEN Ag3 API client>
Storage URL             : gs://vo_agam_release/
Data releases available : 3.0, 3.1, 3.2, 3.3, 3.4, 3.5, 3.6, 3.7, 3.8, 3.9
Results cache           : /content/drive/MyDrive/malariagen_data_cache
Cohorts analysis        : 20240418
AIM analysis            : 20220528
Site filters analysis   : dt_20200416
Software version        : malariagen_data 9.0.0
Client location         : Iowa, US
---
Please note that data are subject to terms of use,
for more information see https://www.malariagen.net/data
or contact support@malariagen.net. For API documentation see 
https://malariagen.github.io/malariagen-data-python/v9.0.0/Ag3.html

## Data Exploration.

For this analysis we shall consider the East African of Uganda. The MalariaGEN data object is a multidimensional array known as an xarray. We can use pandas and MalariaGEN methods to subset the array to extract specific information.

Here we obtain data from the 8th release (3.8). Countries in the dataset are organised at 2 administrative levels. Administrative level 1 `cohort_admin1_year` denote the cardinal regions of a country i.e(North, East, West, South) in a given year. The next administrative level, `cohort_admin2_year`, are subdivisions of the `cohort_admin1_year`. In the context of Uganda, administrative level 2 represent districts.

However, for this analysis we shall restrict our scope to the Eastern region and subset our cohort of samples.



In [ ]:
ag3.plot_samples_interactive_map(
    sample_sets="3.8",
    sample_query="cohort_admin1_year == 'UG-E_gamb_2019'"
)

Map(center=[-2, 20], controls=(ZoomControl(options=['position', 'zoom_in_text', 'zoom_in_title', 'zoom_out_tex…

In [ ]:
# Total number of countries present in the 8th MalariaGEN data release.
df_samples = ag3.sample_metadata(sample_sets="3.8")

pivot_country_year_taxon = (
    df_samples
    .pivot_table(
        index=["country", "year","cohort_admin1_year"],
        columns=["taxon"],
        values="sample_id",
        aggfunc="count",
        fill_value=0
    )
)
pivot_country_year_taxon
# We can see that this release contains data from 4 countries.

taxon                                 arabiensis  coluzzii  fontenillei  \
country      year cohort_admin1_year                                      
Burkina Faso 2011 BF-02_colu_2011              0        18            0   
                  BF-02_gcx4_2011              0         0            0   
             2012 BF-02_colu_2012              0        63            0   
             2015 BF-02_colu_2015              0        33            0   
             2016 BF-02_colu_2016              0        53            0   
             2017 BF-09_arab_2017              7         0            0   
                  BF-09_colu_2017              0        19            0   
                  BF-09_gamb_2017              0         0            0   
             2018 BF-09_arab_2018              9         0            0   
                  BF-09_colu_2018              0        16            0   
                  BF-09_gamb_2018              0         0            0   
             2019 BF-09_arab_2019             36         0            0   
                  BF-09_colu_2019              0        43            0   
                  BF-09_gamb_2019              0         0            0   
Gabon        2019 GA-6_font_2019               0         0           24   
                  GA-6_gamb_2019               0         0            0   
             2020 GA-6_font_2020               0         0           15   
Nigeria      2018 NG-OG_colu_2018              0        15            0   
                  NG-OG_gamb_2018              0         0            0   
                  NG-OY_colu_2018              0         1            0   
                  NG-OY_gamb_2018              0         0            0   
Uganda       2013 UG-C_arab_2013               1         0            0   
                  UG-C_gamb_2013               0         0            0   
             2014 UG-C_gamb_2014               0         0            0   
             2015 UG-C_arab_2015               2         0            0   
                  UG-C_gamb_2015               0         0            0   
             2016 UG-C_gamb_2016               0         0            0   
             2017 UG-C_arab_2017              19         0            0   
                  UG-C_gamb_2017               0         0            0   
                  UG-E_arab_2017              12         0            0   
                  UG-E_gamb_2017               0         0            0   
                  UG-W_arab_2017               5         0            0   
                  UG-W_gamb_2017               0         0            0   
             2018 UG-C_arab_2018              12         0            0   
                  UG-C_gamb_2018               0         0            0   
                  UG-E_arab_2018              59         0            0   
                  UG-E_gamb_2018               0         0            0   
             2019 UG-E_arab_2019              15         0            0   
                  UG-E_gamb_2019               0         0            0   
                  UG-W_arab_2019              11         0            0   
                  UG-W_gamb_2019               0         0            0   

taxon                                 gambiae  gcx4  
country      year cohort_admin1_year                 
Burkina Faso 2011 BF-02_colu_2011           0     0  
                  BF-02_gcx4_2011           0    41  
             2012 BF-02_colu_2012           0     0  
             2015 BF-02_colu_2015           0     0  
             2016 BF-02_colu_2016           0     0  
             2017 BF-09_arab_2017           0     0  
                  BF-09_colu_2017           0     0  
                  BF-09_gamb_2017          15     0  
             2018 BF-09_arab_2018           0     0  
                  BF-09_colu_2018           0     0  
                  BF-09_gamb_2018          18     0  
             2019 BF-09_arab_2019           0     0  
                  

Subsetting for Uganda only reveals that the only species present are Anopheles arabiensis and Anopheles gambiae. Anopheles colluzzi and the cryptic taxon gcx3 are notably missing.

More importanly we can observe that there are 191 *Anopheles gambiae* samples in the Eastern Region cohort, denoted as `UG-E_gamb_2019`.


In [ ]:
# Filtering pivot table to extract Ugandan samples from the 3.8 data release.
df_samples = ag3.sample_metadata(sample_sets="3.8", sample_query="country == 'Uganda'")
pivot_country_year_taxon = (
    df_samples
    .query("year == 2019")
    .pivot_table(
        index=["country", "year","cohort_admin1_year"],
        columns=["taxon"],
        values="sample_id",
        aggfunc="count",
        fill_value=0
    )
)
pivot_country_year_taxon

taxon                            arabiensis  gambiae
country year cohort_admin1_year                     
Uganda  2019 UG-E_arab_2019              15        0
             UG-E_gamb_2019               0      191
             UG-W_arab_2019              11        0
             UG-W_gamb_2019               0       52

Using the `.count_samples` method we can identify the number of mosquitoes that were sampled per district in the Eastern region. We use conditional logic to perform this subsetting. First subset by sample year 2019 and `admin1_iso` UG-E which represents the Eastern Region.

In [ ]:
ag3.count_samples(sample_sets="3.8",
                  sample_query="country == 'Uganda' and year == 2019 and admin1_iso == 'UG-E'"
)

taxon                                               arabiensis  gambiae
country admin1_iso admin1_name    admin2_name year                     
Uganda  UG-E       Eastern Region Bududa      2019           0        3
                                  Bukedea     2019           1        1
                                  Bulambuli   2019           1        3
                                  Busia       2019           1       74
                                  Kaliro      2019           1        0
                                  Kapelebyong 2019           2       15
                                  Manafwa     2019           5       94
                                  Sironko     2019           4        1

## Genome Wide Selection Scans

### H12 Calibration

We perform H12 calibration in order to obtain an appropriate window size to detect selection signal from the GWSS plot. A small window size produces a plot with a ton of noise making it hard to detect signal. A window size to large will result in the loss of selection signal.


What we are looking for in the calibration plot is the x coordinate where the y axis value is  approximately 0.1 .


In [ ]:
# CALIBRATION FOR 2019 EASTERN UGANDAN COHORT
ag3.plot_h12_calibration(
    contig="3L",
    analysis="gamb_colu",
    sample_sets="3.8",
    sample_query="cohort_admin1_year == 'UG-E_gamb_2019'",
)

Load haplotypes:   0%|          | 0/352 [00:00<?, ?it/s]

Compute H12:   0%|          | 0/8 [00:00<?, ?it/s]

### H12 Plot Generation.

In [ ]:
# SELECTION SCAN FOR 2019
for contig in ag3.contigs:
  ag3.plot_h12_gwss(
      contig=contig,
      analysis="gamb_colu",
      window_size=500,
      sample_sets="3.8",
      sample_query="cohort_admin1_year == 'UG-E_gamb_2019'",
      title="EASTERN REGION 2019; window_size=500"
  )

Load haplotypes:   0%|          | 0/552 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/malariagen_data/anoph/h12.py:455: UserWarning: found multiple competing values for 'toolbar.active_drag' property; using the latest value
  fig = bokeh.layouts.gridplot(
/usr/local/lib/python3.10/dist-packages/malariagen_data/anoph/h12.py:455: UserWarning: found multiple competing values for 'toolbar.active_inspect' property; using the latest value
  fig = bokeh.layouts.gridplot(
/usr/local/lib/python3.10/dist-packages/malariagen_data/anoph/h12.py:455: UserWarning: found multiple competing values for 'toolbar.active_scroll' property; using the latest value
  fig = bokeh.layouts.gridplot(


Load haplotypes:   0%|          | 0/456 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/malariagen_data/anoph/h12.py:455: UserWarning: found multiple competing values for 'toolbar.active_drag' property; using the latest value
  fig = bokeh.layouts.gridplot(
/usr/local/lib/python3.10/dist-packages/malariagen_data/anoph/h12.py:455: UserWarning: found multiple competing values for 'toolbar.active_inspect' property; using the latest value
  fig = bokeh.layouts.gridplot(
/usr/local/lib/python3.10/dist-packages/malariagen_data/anoph/h12.py:455: UserWarning: found multiple competing values for 'toolbar.active_scroll' property; using the latest value
  fig = bokeh.layouts.gridplot(


Load haplotypes:   0%|          | 0/464 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/malariagen_data/anoph/h12.py:455: UserWarning: found multiple competing values for 'toolbar.active_drag' property; using the latest value
  fig = bokeh.layouts.gridplot(
/usr/local/lib/python3.10/dist-packages/malariagen_data/anoph/h12.py:455: UserWarning: found multiple competing values for 'toolbar.active_inspect' property; using the latest value
  fig = bokeh.layouts.gridplot(
/usr/local/lib/python3.10/dist-packages/malariagen_data/anoph/h12.py:455: UserWarning: found multiple competing values for 'toolbar.active_scroll' property; using the latest value
  fig = bokeh.layouts.gridplot(


Load haplotypes:   0%|          | 0/352 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/malariagen_data/anoph/h12.py:455: UserWarning: found multiple competing values for 'toolbar.active_drag' property; using the latest value
  fig = bokeh.layouts.gridplot(
/usr/local/lib/python3.10/dist-packages/malariagen_data/anoph/h12.py:455: UserWarning: found multiple competing values for 'toolbar.active_inspect' property; using the latest value
  fig = bokeh.layouts.gridplot(
/usr/local/lib/python3.10/dist-packages/malariagen_data/anoph/h12.py:455: UserWarning: found multiple competing values for 'toolbar.active_scroll' property; using the latest value
  fig = bokeh.layouts.gridplot(


Load haplotypes:   0%|          | 0/208 [00:00<?, ?it/s]

/usr/local/lib/python3.10/dist-packages/malariagen_data/anoph/h12.py:455: UserWarning: found multiple competing values for 'toolbar.active_drag' property; using the latest value
  fig = bokeh.layouts.gridplot(
/usr/local/lib/python3.10/dist-packages/malariagen_data/anoph/h12.py:455: UserWarning: found multiple competing values for 'toolbar.active_inspect' property; using the latest value
  fig = bokeh.layouts.gridplot(
/usr/local/lib/python3.10/dist-packages/malariagen_data/anoph/h12.py:455: UserWarning: found multiple competing values for 'toolbar.active_scroll' property; using the latest value
  fig = bokeh.layouts.gridplot(


Interrogation of the genomic coordinates surrounding the peaks found per chromosome in the GWSS.

In [ ]:
# CHROMOSOME 2R PEAKS
CHROM2R_P1_df = (
    ag3.genome_features(region="2R:18,500,000-19,000,000")
    .query('type == "gene"')
    [["contig", "start", "end", "ID", "Name", "description"]]
    .set_index("ID")
)

CHROM2R_P2_df = (
    ag3.genome_features(region="2R:27,500,000-30,000,000")
    .query('type == "gene"')
    [["contig", "start", "end", "ID", "Name", "description"]]
    .set_index("ID")
)

# CHROMOSOME 2L PEAKS
CHROM2L_P1_df = (
    ag3.genome_features(region="2L:22,500,000-23,000,000")
    .query('type == "gene"')
    [["contig", "start", "end", "ID", "Name", "description"]]
    .set_index("ID")
)

CHROM2L_P2_df = (
    ag3.genome_features(region="2L:33,500,000-34,500,000")
    .query('type == "gene"')
    [["contig", "start", "end", "ID", "Name", "description"]]
    .set_index("ID")
)

# CHROMOSOME 3R PEAK.
CHROM3R_P1_df = (
    ag3.genome_features(region="3R:28,500,000 -29,000,000")
    .query('type == "gene"')
    [["contig", "start", "end", "ID", "Name", "description"]]
    .set_index("ID")
)



The code below susequently saves the identified genes per H12 peak in an appropriate tsv file.

In [ ]:
# Saving genes at H12 peaks to tsv files.
CHROM2R_P1_df.to_csv('2R_P1.tsv', sep="\t")
CHROM2R_P2_df.to_csv('2R_P2.tsv', sep="\t")
CHROM2L_P1_df.to_csv('2L_P1.tsv', sep="\t")
CHROM2L_P2_df.to_csv('2L_P2.tsv', sep="\t")
CHROM3R_P1_df.to_csv('3R_P1.tsv', sep="\t")

## Candidate Resistance Genes.

### Chromosome 2R

#### Peak1
Gr2 - Gustatory receptor 2
The Gustatory Receptor (GR) is a gene family associated with chemoreception in insects. These genes are expressed in gustatory receptor neurons, which have dendritic processes located in various parts of a mosquito's body. When triggered by specific chemicals, they initiate action potentials that are transmitted to the taste centers in the brain, allowing mosquitoes to interact with their environment. This capability is crucial for their feeding process, egg-laying, and identification of conspecifics(Sparks et al., 2013).


ABCB1 - ATP-binding cassette transporter(ABS transporter) family B member 1

Part of the ATP-binding cassette superfamily of genes, they are implicated in the transportation of substrates across cell membranes and play a role in detoxifying pesticides and plant secondary metabolites. The ABCB1 family B gives rise to the transporter P-glycoprotein. However, it is difficult to predict what kinds of substrates each member of the transporter family of genes carries. Limited research is available elucidating the specific function of this gene in *Anopheles gambiae*, and pesticide transport work has only been done in the model organism *Drosophila melanogaster* (Denecke et al., 2022).



#### Peak2

GPRMGL4 - G protein-coupled receptors are a class of transmembrane proteins that are involved in signal transduction.

COEAE6O

This gene belongs to the serine esterase family of enzymes. These kinds of enzymes are known for their acylation-deacylation activity. Most classes of enzymes bare ester groups in their chemical structure. As a consequence, these enzymes are involved in metabolic resistance mechanisms. However the strength of resistance conferred is an order of magnitude less than target-site resistance (Labbé et al., 2017)



CYP Gene Cluster: (CYP6Z4,CYP6AA1,CYP6AA2,CYP6P15P,CYP6AD1,CYP6P1,CYP6P2,CYP6P3,CYP6P4,CYP6P5)

CYP or the Cytochrome P450 monooxygenases are heme-thiolate enzymes found in most organisms and in insects they are known to metabolise endogenous compounds such as hormones and xenobiotics like plant secondary metabolites, pollutants and insecticides. Insecticide resistance is thought to arise via the amplification or upregulation of multiple P450s. Additionally, P450s have been implicated to confer resistance of multiple classes of insecticides such as organochorines(DDT), pyrethroids and carbamates. (Labbé et al., 2017)


### Chromosome 3R

#### Peak1
Genes: (GSTE1, GSTE2, GSTE3, GSTE4, GSTE5, GSTE6, GSTE7, GSTE8)

The GSTE (glutathione S-transferase) family of genes is a standout feature at the H12 peak on Chromosome 3R. GST enzymes, present in most insects, have a broad range of detoxification capabilities. They are primarily associated with resistance to organochlorines (such as DDT), organophosphates (for example, pirimiphos methyl), and pyrethroids (like deltamethrin). This is believed to result from the duplication and upregulation of these genes. A QTL analysis of the GST cluster found that GSTE2 metabolizes DDT. One proposed mechanism is that GST genes confer resistance to pyrethroids through sequestration(Labbé et al., 2017).



**References:**
1. Labbé, P., David, J.-P., Alout, H., Milesi, P., Djogbénou, L., Pasteur, N., & Weill, M. (2017). Evolution of Resistance to Insecticide in Disease Vectors. In *Genetics and Evolution of Infectious Diseases* (pp. 313–339). Elsevier. https://doi.org/10.1016/B978-0-12-799942-5.00014-7

2. Denecke, S., Bảo Lương, H. N., Koidou, V., Kalogeridi, M., Socratous, R., Howe, S., Vogelsang, K., Nauen, R., Batterham, P., Geibel, S., & Vontas, J. (n.d.). Characterization of a novel pesticide transporter and P-glycoprotein orthologues in Drosophila melanogaster. *Proceedings of the Royal Society B: Biological Sciences*, *289*(1975), 20220625. https://doi.org/10.1098/rspb.2022.0625

3. Sparks, J. T., Vinyard, B. T., & Dickens, J. C. (2013). Gustatory receptor expression in the labella and tarsi of *Aedes aegypti*. *Insect Biochemistry and Molecular Biology*, *43*(12), 1161–1171. https://doi.org/10.1016/j.ibmb.2013.10.005
